In [6]:
# MAV Route Analysis - Updated for Google Cloud Storage
# Fixed version that loads data from GCS bucket instead of local files

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import re
import json
import os
from datetime import datetime, timedelta
from google.cloud import storage

print("🚆 MAV Route Analysis - Starting...")
print("📊 Loading data from Google Cloud Storage bucket...")

def load_compact_files_from_gcs(bucket_name='mpt-all-sources', date='2025-07-19'):
    """Load compact JSON files from Google Cloud Storage bucket."""
    
    # Initialize GCS client
    client = storage.Client()
    bucket = client.bucket(bucket_name)
    
    # Define the path in the bucket
    gcs_prefix = f"blog/mav/json_output/{date}/"
    
    print(f"🔍 Looking for files in: gs://{bucket_name}/{gcs_prefix}")
    
    # List all blobs with the prefix
    blobs = bucket.list_blobs(prefix=gcs_prefix)
    
    # Filter for compact JSON files
    compact_blobs = []
    for blob in blobs:
        if blob.name.endswith('_compact.json'):
            compact_blobs.append(blob)
    
    if not compact_blobs:
        print(f"❌ No compact JSON files found in: {gcs_prefix}")
        return []
    
    print(f"✅ Found {len(compact_blobs)} files in: {gcs_prefix}")
    
    # Parse filenames to extract station pairs and timestamps
    file_info = []
    for blob in compact_blobs:
        filename = blob.name.split('/')[-1]  # Get just the filename
        
        # Parse pattern: bulk_START_END_YYYYMMDD_HHMMSS_compact.json
        match = re.match(r'bulk_(\d+)_(\d+)_(\d{8}_\d{6})_compact\.json', filename)
        if match:
            start_station, end_station, timestamp = match.groups()
            
            # Download and parse JSON content
            try:
                json_content = json.loads(blob.download_as_text())
                
                file_info.append({
                    'blob': blob,
                    'filename': filename,
                    'start_station': start_station,
                    'end_station': end_station,
                    'timestamp': timestamp,
                    'station_pair': f"{start_station}_{end_station}",
                    'data': json_content
                })
            except Exception as e:
                print(f"⚠️ Error loading {filename}: {e}")
                continue
    
    print(f"Successfully parsed {len(file_info)} files")
    print("Sample file info:")
    for info in file_info[:3]:
        print(f"  {info['station_pair']} @ {info['timestamp']}")
    
    return file_info

# Load files from the most recent date available
print("📊 Loading MAV route data from Google Cloud Storage...")
files = load_compact_files_from_gcs(date='2025-07-19')

if not files:
    print("❌ No files found for 2025-07-19. Trying alternative dates...")
    # Try previous days if current day has no data
    for days_back in range(1, 8):
        alt_date = (datetime.now() - timedelta(days=days_back)).strftime('%Y-%m-%d')
        print(f"🔍 Trying date: {alt_date}")
        files = load_compact_files_from_gcs(date=alt_date)
        if files:
            print(f"✅ Found data for {alt_date}")
            break
    
    if not files:
        print("❌ No data found in the last 7 days!")
        raise Exception("No MAV route data available")

print(f"🎯 Successfully loaded {len(files)} route files for analysis")


🚆 MAV Route Analysis - Starting...
📊 Loading data from Google Cloud Storage bucket...
📊 Loading MAV route data from Google Cloud Storage...
🔍 Looking for files in: gs://mpt-all-sources/blog/mav/json_output/2025-07-19/
✅ Found 232 files in: blog/mav/json_output/2025-07-19/
Successfully parsed 232 files
Sample file info:
  004250274_005513821 @ 20250719_203039
  004250274_005513821 @ 20250719_203040
  004252667_005512880 @ 20250719_202939
🎯 Successfully loaded 232 route files for analysis


In [7]:
import json
import pandas as pd
import numpy as np
import os
import glob
from datetime import datetime
import matplotlib.pyplot as plt
import seaborn as sns
from collections import defaultdict
import re

print("Libraries loaded successfully!")

# Set up plotting style
plt.style.use('default')
sns.set_palette("husl")


Libraries loaded successfully!


In [8]:
import re
import json
from google.cloud import storage

def load_compact_files_from_gcs(bucket_name='mpt-all-sources', date='2025-07-19'):
    """Load compact JSON files from Google Cloud Storage bucket."""
    
    # Initialize GCS client
    client = storage.Client()
    bucket = client.bucket(bucket_name)
    
    # Define the path in the bucket
    gcs_prefix = f"blog/mav/json_output/{date}/"
    
    print(f"🔍 Looking for files in: gs://{bucket_name}/{gcs_prefix}")
    
    # List all blobs with the prefix
    blobs = bucket.list_blobs(prefix=gcs_prefix)
    
    # Filter for compact JSON files
    compact_blobs = []
    for blob in blobs:
        if blob.name.endswith('_compact.json'):
            compact_blobs.append(blob)
    
    if not compact_blobs:
        print(f"❌ No compact JSON files found in: {gcs_prefix}")
        return []
    
    print(f"✅ Found {len(compact_blobs)} files in: {gcs_prefix}")
    
    # Parse filenames to extract station pairs and timestamps
    file_info = []
    for blob in compact_blobs:
        filename = blob.name.split('/')[-1]  # Get just the filename
        
        # Parse pattern: bulk_START_END_YYYYMMDD_HHMMSS_compact.json
        match = re.match(r'bulk_(\d+)_(\d+)_(\d{8}_\d{6})_compact\.json', filename)
        if match:
            start_station, end_station, timestamp = match.groups()
            
            # Download and parse JSON content
            json_content = json.loads(blob.download_as_text())
            
            file_info.append({
                'blob': blob,
                'filename': filename,
                'start_station': start_station,
                'end_station': end_station,
                'timestamp': timestamp,
                'station_pair': f"{start_station}_{end_station}",
                'data': json_content
            })
    
    print(f"Successfully parsed {len(file_info)} files")
    print("Sample file info:")
    for info in file_info[:3]:
        print(f"  {info['station_pair']} @ {info['timestamp']}")
    
    return file_info

files = load_compact_files_from_gcs(date='2025-07-19')
for f in files:
    routes = f['data']  # This is your JSON data
    pair = f['station_pair']  # e.g., "004301974_005510009"

🔍 Looking for files in: gs://mpt-all-sources/blog/mav/json_output/2025-07-19/
✅ Found 232 files in: blog/mav/json_output/2025-07-19/
Successfully parsed 232 files
Sample file info:
  004250274_005513821 @ 20250719_203039
  004250274_005513821 @ 20250719_203040
  004252667_005512880 @ 20250719_202939


In [9]:
files

[{'blob': <Blob: mpt-all-sources, blog/mav/json_output/2025-07-19/bulk_004250274_005513821_20250719_203039_compact.json, 1752957732790697>,
  'filename': 'bulk_004250274_005513821_20250719_203039_compact.json',
  'start_station': '004250274',
  'end_station': '005513821',
  'timestamp': '20250719_203039',
  'station_pair': '004250274_005513821',
  'data': {'success': True,
   'timestamp': '2025-07-19T20:30:44.426624',
   'route_info': {'start_station': '004250274',
    'end_station': '005513821',
    'travel_date': None},
   'statistics': {'total_trains': 5,
    'average_delay': 0.0,
    'max_delay': 0,
    'trains_on_time': 5,
    'trains_delayed': 0,
    'trains_significantly_delayed': 0,
    'on_time_percentage': 100.0,
    'delayed_percentage': 0.0},
   'routes': [{'train_name': '36562',
     'departure_time': '09:38',
     'departure_time_actual': '09:43',
     'departure_iso': '2025-07-19T09:38:00+02:00',
     'arrival_time': '11:29',
     'arrival_time_actual': '11:28',
     'ar

In [10]:
# ========================= BUDAPEST ↔ RAJKA UNIQUE PAIRS =========================

def extract_budapest_rajka_pairs_fixed():
    """
    FIXED: Extract unique Budapest-Rajka pairs by parsing route headers correctly.
    The source/destination columns have parsing errors, so we use route_header instead.
    """
    print("🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)")
    print("="*60)
    
    # First, let's read the generated CSV file
    import glob
    
    # Find the most recent CSV file
    csv_files = glob.glob("mav_route_pairs_full_*.csv")
    if not csv_files:
        print("❌ No CSV files found. Please run the extraction first.")
        return None, None
    
    latest_csv = max(csv_files, key=lambda x: x.split('_')[-1])
    print(f"📂 Reading data from: {latest_csv}")
    
    # Read the CSV
    df_full = pd.read_csv(latest_csv, encoding='utf-8')
    print(f"📊 Total records in CSV: {len(df_full)}")
    
    # Show sample problematic data
    print(f"\n🔍 SAMPLE DATA (showing the parsing issues):")
    sample_data = df_full.head(3)
    for _, row in sample_data.iterrows():
        print(f"   Route: {row['route_header']}")
        print(f"   Source: {row['source']} (WRONG)")
        print(f"   Dest: {row['destination']} (WRONG)")
        print()
    
    print("💡 SOLUTION: Parse route headers directly instead of using source/destination")
    
    # Parse route headers directly
    unique_routes = {}
    all_route_data = []
    
    for _, row in df_full.iterrows():
        route_header = str(row.get('route_header', ''))
        
        # Only process Budapest-Rajka routes
        if not ('budapest' in route_header.lower() and 
               ('rajka' in route_header.lower() or 'hegyeshalom' in route_header.lower())):
            continue
        
        print(f"🔍 Processing: {route_header}")
        
        # Parse route header like "1 Budapest — Hegyeshalom — Rajka"
        if '—' in route_header or '–' in route_header:
            # Clean and split the route
            clean_route = route_header.replace('—', '–')
            parts = [part.strip() for part in clean_route.split('–')]
            
            if len(parts) >= 2:
                # Remove leading numbers from first part
                start_station = re.sub(r'^\d+\s+', '', parts[0]).strip()
                end_station = parts[-1].strip()
                
                print(f"   ✅ Parsed: {start_station} → {end_station}")
                
                # Create unique route key
                route_key = f"{start_station} → {end_station}"
                
                route_data = {
                    'route_header': route_header,
                    'start_station': start_station,
                    'end_station': end_station,
                    'page': row.get('page', 'N/A'),
                    'total_stations': row.get('total_stations', 'N/A'),
                    'route_key': route_key
                }
                
                all_route_data.append(route_data)
                
                # Track unique routes
                if route_key not in unique_routes:
                    unique_routes[route_key] = {
                        'start': start_station,
                        'end': end_station,
                        'count': 1,
                        'sample_route': route_header,
                        'pages': [row.get('page', 'N/A')],
                        'station_counts': [row.get('total_stations', 'N/A')]
                    }
                else:
                    unique_routes[route_key]['count'] += 1
                    unique_routes[route_key]['pages'].append(row.get('page', 'N/A'))
                    unique_routes[route_key]['station_counts'].append(row.get('total_stations', 'N/A'))
    
    return all_route_data, unique_routes

# Extract the pairs using the FIXED function
all_pairs, unique_pairs = extract_budapest_rajka_pairs_fixed()

print(f"\n🎯 FOUND {len(all_pairs)} BUDAPEST-RAJKA ROUTE ENTRIES")

if unique_pairs:
    print(f"\n🚂 UNIQUE BUDAPEST ↔ RAJKA PAIRS (Order Matters):")
    print("="*70)
    
    # Sort by start station name for better organization
    sorted_pairs = sorted(unique_pairs.items(), key=lambda x: x[1]['start'])
    
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        start = info['start']
        end = info['end'] 
        count = info['count']
        sample = info['sample_route']
        pages = info['pages'][:5]  # Show first 5 pages
        
        print(f"{i:2d}. {start} → {end}")
        print(f"    📊 Found {count} route instance(s)")
        print(f"    📄 Pages: {pages}")
        print(f"    🔗 Sample route: {sample}")
        print(f"    📏 Station counts: {info['station_counts'][:5]}")
        print()
    
    # Create DataFrame for the clean results
    unique_df = pd.DataFrame([
        {
            'direction': direction,
            'start_station': info['start'],
            'end_station': info['end'],
            'route_count': info['count'],
            'sample_route_header': info['sample_route'],
            'pages': ', '.join(map(str, info['pages'][:10])),  # First 10 pages as string
            'avg_stations': sum([x for x in info['station_counts'] if str(x).isdigit()]) / len([x for x in info['station_counts'] if str(x).isdigit()]) if [x for x in info['station_counts'] if str(x).isdigit()] else 0
        }
        for direction, info in unique_pairs.items()
    ])
    
    print(f"📊 SUMMARY STATISTICS:")
    print(f"   - Total unique directions: {len(unique_pairs)}")
    print(f"   - Total route instances: {sum(info['count'] for info in unique_pairs.values())}")
    if len(unique_df) > 0 and unique_df['avg_stations'].mean() > 0:
        print(f"   - Average stations per route: {unique_df['avg_stations'].mean():.1f}")
    
    # Save unique pairs to CSV
    timestamp = dt.datetime.now().strftime("%Y%m%d_%H%M%S")
    output_file = f"budapest_rajka_unique_pairs_{timestamp}.csv"
    unique_df.to_csv(output_file, index=False, encoding='utf-8')
    print(f"   💾 Saved to: {output_file}")
    
    # Show specifically Budapest → Rajka and Rajka → Budapest
    print(f"\n🎯 SPECIFIC BUDAPEST ↔ RAJKA DIRECTIONAL ANALYSIS:")
    
    budapest_to_rajka = []
    rajka_to_budapest = []
    
    for direction, info in unique_pairs.items():
        start_lower = info['start'].lower()
        end_lower = info['end'].lower()
        
        # Budapest → Rajka/Hegyeshalom
        if 'budapest' in start_lower and ('rajka' in end_lower or 'hegyeshalom' in end_lower):
            budapest_to_rajka.append(info)
        
        # Rajka/Hegyeshalom → Budapest  
        elif ('rajka' in start_lower or 'hegyeshalom' in start_lower) and 'budapest' in end_lower:
            rajka_to_budapest.append(info)
    
    print(f"   🔄 Budapest → Rajka/Hegyeshalom directions: {len(budapest_to_rajka)}")
    for pair in budapest_to_rajka:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    print(f"   🔄 Rajka/Hegyeshalom → Budapest directions: {len(rajka_to_budapest)}")  
    for pair in rajka_to_budapest:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    # Show the actual clean station pairs you wanted
    print(f"\n✅ FINAL ANSWER - UNIQUE BUDAPEST ↔ RAJKA PAIRS:")
    print("="*50)
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        print(f"{i}. {info['start']} → {info['end']}")
    
    print(f"\n🎉 SUCCESS! Found {len(unique_pairs)} unique directional pairs")
    print(f"📂 Detailed data saved to: {output_file}")
else:
    print("❌ No Budapest-Rajka pairs found. Check the data extraction.")


🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)
❌ No CSV files found. Please run the extraction first.


TypeError: object of type 'NoneType' has no len()

In [ ]:
# ========================= BUDAPEST ↔ RAJKA UNIQUE PAIRS =========================

def extract_budapest_rajka_pairs_fixed():
    """
    FIXED: Extract unique Budapest-Rajka pairs by parsing route headers correctly.
    The source/destination columns have parsing errors, so we use route_header instead.
    """
    print("🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)")
    print("="*60)
    
    # First, let's read the generated CSV file
    import glob
    
    # Find the most recent CSV file
    csv_files = glob.glob("mav_route_pairs_full_*.csv")
    if not csv_files:
        print("❌ No CSV files found. Please run the extraction first.")
        return None, None
    
    latest_csv = max(csv_files, key=lambda x: x.split('_')[-1])
    print(f"📂 Reading data from: {latest_csv}")
    
    # Read the CSV
    df_full = pd.read_csv(latest_csv, encoding='utf-8')
    print(f"📊 Total records in CSV: {len(df_full)}")
    
    # Show sample problematic data
    print(f"\n🔍 SAMPLE DATA (showing the parsing issues):")
    sample_data = df_full.head(3)
    for _, row in sample_data.iterrows():
        print(f"   Route: {row['route_header']}")
        print(f"   Source: {row['source']} (WRONG)")
        print(f"   Dest: {row['destination']} (WRONG)")
        print()
    
    print("💡 SOLUTION: Parse route headers directly instead of using source/destination")
    
    # Parse route headers directly
    unique_routes = {}
    all_route_data = []
    
    for _, row in df_full.iterrows():
        route_header = str(row.get('route_header', ''))
        
        # Only process Budapest-Rajka routes
        if not ('budapest' in route_header.lower() and 
               ('rajka' in route_header.lower() or 'hegyeshalom' in route_header.lower())):
            continue
        
        print(f"🔍 Processing: {route_header}")
        
        # Parse route header like "1 Budapest — Hegyeshalom — Rajka"
        if '—' in route_header or '–' in route_header:
            # Clean and split the route
            clean_route = route_header.replace('—', '–')
            parts = [part.strip() for part in clean_route.split('–')]
            
            if len(parts) >= 2:
                # Remove leading numbers from first part
                start_station = re.sub(r'^\d+\s+', '', parts[0]).strip()
                end_station = parts[-1].strip()
                
                print(f"   ✅ Parsed: {start_station} → {end_station}")
                
                # Create unique route key
                route_key = f"{start_station} → {end_station}"
                
                route_data = {
                    'route_header': route_header,
                    'start_station': start_station,
                    'end_station': end_station,
                    'page': row.get('page', 'N/A'),
                    'total_stations': row.get('total_stations', 'N/A'),
                    'route_key': route_key
                }
                
                all_route_data.append(route_data)
                
                # Track unique routes
                if route_key not in unique_routes:
                    unique_routes[route_key] = {
                        'start': start_station,
                        'end': end_station,
                        'count': 1,
                        'sample_route': route_header,
                        'pages': [row.get('page', 'N/A')],
                        'station_counts': [row.get('total_stations', 'N/A')]
                    }
                else:
                    unique_routes[route_key]['count'] += 1
                    unique_routes[route_key]['pages'].append(row.get('page', 'N/A'))
                    unique_routes[route_key]['station_counts'].append(row.get('total_stations', 'N/A'))
    
    return all_route_data, unique_routes

# Extract the pairs using the FIXED function
all_pairs, unique_pairs = extract_budapest_rajka_pairs_fixed()

print(f"\n🎯 FOUND {len(all_pairs)} BUDAPEST-RAJKA ROUTE ENTRIES")

if unique_pairs:
    print(f"\n🚂 UNIQUE BUDAPEST ↔ RAJKA PAIRS (Order Matters):")
    print("="*70)
    
    # Sort by start station name for better organization
    sorted_pairs = sorted(unique_pairs.items(), key=lambda x: x[1]['start'])
    
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        start = info['start']
        end = info['end'] 
        count = info['count']
        sample = info['sample_route']
        pages = info['pages'][:5]  # Show first 5 pages
        
        print(f"{i:2d}. {start} → {end}")
        print(f"    📊 Found {count} route instance(s)")
        print(f"    📄 Pages: {pages}")
        print(f"    🔗 Sample route: {sample}")
        print(f"    📏 Station counts: {info['station_counts'][:5]}")
        print()
    
    # Create DataFrame for the clean results
    unique_df = pd.DataFrame([
        {
            'direction': direction,
            'start_station': info['start'],
            'end_station': info['end'],
            'route_count': info['count'],
            'sample_route_header': info['sample_route'],
            'pages': ', '.join(map(str, info['pages'][:10])),  # First 10 pages as string
            'avg_stations': sum([x for x in info['station_counts'] if str(x).isdigit()]) / len([x for x in info['station_counts'] if str(x).isdigit()]) if [x for x in info['station_counts'] if str(x).isdigit()] else 0
        }
        for direction, info in unique_pairs.items()
    ])
    
    print(f"📊 SUMMARY STATISTICS:")
    print(f"   - Total unique directions: {len(unique_pairs)}")
    print(f"   - Total route instances: {sum(info['count'] for info in unique_pairs.values())}")
    if len(unique_df) > 0 and unique_df['avg_stations'].mean() > 0:
        print(f"   - Average stations per route: {unique_df['avg_stations'].mean():.1f}")
    
    # Save unique pairs to CSV
    timestamp = dt.datetime.now().strftime("%Y%m%d_%H%M%S")
    output_file = f"budapest_rajka_unique_pairs_{timestamp}.csv"
    unique_df.to_csv(output_file, index=False, encoding='utf-8')
    print(f"   💾 Saved to: {output_file}")
    
    # Show specifically Budapest → Rajka and Rajka → Budapest
    print(f"\n🎯 SPECIFIC BUDAPEST ↔ RAJKA DIRECTIONAL ANALYSIS:")
    
    budapest_to_rajka = []
    rajka_to_budapest = []
    
    for direction, info in unique_pairs.items():
        start_lower = info['start'].lower()
        end_lower = info['end'].lower()
        
        # Budapest → Rajka/Hegyeshalom
        if 'budapest' in start_lower and ('rajka' in end_lower or 'hegyeshalom' in end_lower):
            budapest_to_rajka.append(info)
        
        # Rajka/Hegyeshalom → Budapest  
        elif ('rajka' in start_lower or 'hegyeshalom' in start_lower) and 'budapest' in end_lower:
            rajka_to_budapest.append(info)
    
    print(f"   🔄 Budapest → Rajka/Hegyeshalom directions: {len(budapest_to_rajka)}")
    for pair in budapest_to_rajka:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    print(f"   🔄 Rajka/Hegyeshalom → Budapest directions: {len(rajka_to_budapest)}")  
    for pair in rajka_to_budapest:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    # Show the actual clean station pairs you wanted
    print(f"\n✅ FINAL ANSWER - UNIQUE BUDAPEST ↔ RAJKA PAIRS:")
    print("="*50)
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        print(f"{i}. {info['start']} → {info['end']}")
    
    print(f"\n🎉 SUCCESS! Found {len(unique_pairs)} unique directional pairs")
    print(f"📂 Detailed data saved to: {output_file}")
else:
    print("❌ No Budapest-Rajka pairs found. Check the data extraction.")


🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)
❌ No CSV files found. Please run the extraction first.


TypeError: object of type 'NoneType' has no len()

In [ ]:
# For each station pair, keep only the latest file
latest_files = {}
for info in file_info:
    pair = info['station_pair']
    timestamp = info['timestamp']
    
    if pair not in latest_files or timestamp > latest_files[pair]['timestamp']:
        latest_files[pair] = info

print(f"Selected {len(latest_files)} latest files for distinct station pairs")

# Load JSON data from selected files
route_data = []
failed_loads = []

for pair, info in latest_files.items():
    try:
        # Try UTF-8 first, fallback to other encodings if needed
        encodings_to_try = ['utf-8', 'utf-8-sig', 'latin1', 'cp1252']
        
        data = None
        for encoding in encodings_to_try:
            try:
                with open(info['file_path'], 'r', encoding=encoding) as f:
                    data = json.load(f)
                break
            except UnicodeDecodeError:
                continue
                
        if data and data.get('success') and data.get('routes'):
            # Add station pair info to the data
            data['station_pair'] = pair
            data['start_station'] = info['start_station']
            data['end_station'] = info['end_station']
            data['file_timestamp'] = info['timestamp']
            route_data.append(data)
        else:
            failed_loads.append(f"{pair}: No routes found")
            
    except Exception as e:
        failed_loads.append(f"{pair}: {str(e)}")

print(f"Successfully loaded {len(route_data)} route datasets")
if failed_loads:
    print(f"Failed to load {len(failed_loads)} files:")
    for fail in failed_loads[:3]:  # Show first 3 failures
        print(f"  {fail}")


Selected 0 latest files for distinct station pairs
Successfully loaded 0 route datasets


In [ ]:
# Extract final leg arrival data from each route
final_arrivals = []

for data in route_data:
    station_pair = data['station_pair']
    start_station = data['start_station']
    end_station = data['end_station']
    
    for route_idx, route in enumerate(data['routes']):
        # Get route segments - the final leg is the last segment
        segments = route.get('route_segments', [])
        
        if segments:
            final_leg = segments[-1]  # Last segment = final leg
            
            arrival_info = {
                'station_pair': station_pair,
                'start_station': start_station,
                'end_station': end_station,
                'route_idx': route_idx,
                'train_name': route.get('train_name', 'Unknown'),
                'total_travel_time': route.get('travel_time_min', 'Unknown'),
                'total_transfers': route.get('transfers_count', 0),
                'total_price_huf': route.get('price_huf', None),
                
                # Final leg info
                'final_leg_train': final_leg.get('train_full_name', 'Unknown'),
                'final_leg_from': final_leg.get('start_station', 'Unknown'),
                'final_leg_to': final_leg.get('end_station', 'Unknown'),
                
                # Final leg arrival data (what user specifically wanted)
                'arrival_scheduled': final_leg.get('arrival_scheduled', 'Unknown'),
                'arrival_actual': final_leg.get('arrival_actual', 'Unknown'),
                'arrival_delay': final_leg.get('arrival_delay', 0),
                
                # Additional timing info
                'departure_scheduled': final_leg.get('departure_scheduled', 'Unknown'),
                'departure_actual': final_leg.get('departure_actual', 'Unknown'),
                'departure_delay': final_leg.get('departure_delay', 0),
                'leg_travel_time': final_leg.get('travel_time', 'Unknown'),
                'has_delays': final_leg.get('has_delays', False)
            }
            
            final_arrivals.append(arrival_info)

print(f"Extracted final leg data for {len(final_arrivals)} routes")

# Convert to DataFrame for analysis
df = pd.DataFrame(final_arrivals)
print(f"DataFrame shape: {df.shape}")
print("\nColumns:", list(df.columns))


Extracted final leg data for 0 routes
DataFrame shape: (0, 0)

Columns: []


In [ ]:
# Basic statistics about final leg arrivals
print("=== FINAL LEG ARRIVAL ANALYSIS ===\n")

if len(df) == 0:
    print("❌ No data to analyze! Check if JSON files were loaded correctly.")
else:
    print("1. ARRIVAL DELAY SUMMARY:")
    print(f"   Total routes analyzed: {len(df)}")
    print(f"   Routes with delays: {len(df[df['arrival_delay'] > 0])}")
    print(f"   Routes on time: {len(df[df['arrival_delay'] == 0])}")
    print(f"   Routes arriving early: {len(df[df['arrival_delay'] < 0])}")

    print(f"\n   Average arrival delay: {df['arrival_delay'].mean():.1f} minutes")
    print(f"   Max arrival delay: {df['arrival_delay'].max()} minutes")
    print(f"   Min arrival delay: {df['arrival_delay'].min()} minutes")

    print("\n2. DELAY DISTRIBUTION:")
    delay_counts = df['arrival_delay'].value_counts().sort_index()
    print(delay_counts.head(10))

    print("\n3. SAMPLE DATA (first 5 routes):")
    print(df[['station_pair', 'final_leg_train', 'arrival_scheduled', 'arrival_actual', 'arrival_delay']].head())


=== FINAL LEG ARRIVAL ANALYSIS ===

❌ No data to analyze! Check if JSON files were loaded correctly.


In [ ]:
# Simple visualization of delays if we have data
if len(df) > 0:
    print("=== DELAY VISUALIZATIONS ===\n")
    
    # Create a simple plot
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15, 5))
    
    # Plot 1: Delay distribution
    df['arrival_delay'].hist(bins=30, ax=ax1, alpha=0.7)
    ax1.set_title('Final Leg Arrival Delay Distribution')
    ax1.set_xlabel('Delay (minutes)')
    ax1.set_ylabel('Number of Routes')
    ax1.axvline(0, color='red', linestyle='--', alpha=0.5, label='On Time')
    ax1.legend()
    
    # Plot 2: Delay by number of transfers
    delay_by_transfers = df.groupby('total_transfers')['arrival_delay'].mean()
    delay_by_transfers.plot(kind='bar', ax=ax2, alpha=0.7)
    ax2.set_title('Average Final Leg Delay by Number of Transfers')
    ax2.set_xlabel('Number of Transfers')
    ax2.set_ylabel('Average Delay (minutes)')
    ax2.tick_params(axis='x', rotation=0)
    
    plt.tight_layout()
    plt.show()
    
    # Summary statistics
    print(f"📊 Key Insights:")
    print(f"   • {len(df[df['arrival_delay'] == 0])/len(df)*100:.1f}% of routes arrive exactly on time")
    print(f"   • {len(df[df['arrival_delay'] > 0])/len(df)*100:.1f}% of routes are delayed") 
    print(f"   • {len(df[df['arrival_delay'] < 0])/len(df)*100:.1f}% of routes arrive early")
    
    # Show routes with longest delays
    if len(df[df['arrival_delay'] > 0]) > 0:
        print(f"\n🚨 Most delayed routes (final leg):")
        worst_delays = df.nlargest(3, 'arrival_delay')[['station_pair', 'final_leg_train', 'arrival_scheduled', 'arrival_actual', 'arrival_delay']]
        for _, row in worst_delays.iterrows():
            print(f"   • {row['station_pair']}: {row['final_leg_train']} - {row['arrival_delay']} min delay")
else:
    print("❌ No data loaded - cannot create visualizations")


❌ No data loaded - cannot create visualizations


In [ ]:
# ========================= BUDAPEST ↔ RAJKA UNIQUE PAIRS =========================

def extract_budapest_rajka_pairs_fixed():
    """
    FIXED: Extract unique Budapest-Rajka pairs by parsing route headers correctly.
    The source/destination columns have parsing errors, so we use route_header instead.
    """
    print("🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)")
    print("="*60)
    
    # First, let's read the generated CSV file
    import glob
    
    # Find the most recent CSV file
    csv_files = glob.glob("mav_route_pairs_full_*.csv")
    if not csv_files:
        print("❌ No CSV files found. Please run the extraction first.")
        return None, None
    
    latest_csv = max(csv_files, key=lambda x: x.split('_')[-1])
    print(f"📂 Reading data from: {latest_csv}")
    
    # Read the CSV
    df_full = pd.read_csv(latest_csv, encoding='utf-8')
    print(f"📊 Total records in CSV: {len(df_full)}")
    
    # Show sample problematic data
    print(f"\n🔍 SAMPLE DATA (showing the parsing issues):")
    sample_data = df_full.head(3)
    for _, row in sample_data.iterrows():
        print(f"   Route: {row['route_header']}")
        print(f"   Source: {row['source']} (WRONG)")
        print(f"   Dest: {row['destination']} (WRONG)")
        print()
    
    print("💡 SOLUTION: Parse route headers directly instead of using source/destination")
    
    # Parse route headers directly
    unique_routes = {}
    all_route_data = []
    
    for _, row in df_full.iterrows():
        route_header = str(row.get('route_header', ''))
        
        # Only process Budapest-Rajka routes
        if not ('budapest' in route_header.lower() and 
               ('rajka' in route_header.lower() or 'hegyeshalom' in route_header.lower())):
            continue
        
        print(f"🔍 Processing: {route_header}")
        
        # Parse route header like "1 Budapest — Hegyeshalom — Rajka"
        if '—' in route_header or '–' in route_header:
            # Clean and split the route
            clean_route = route_header.replace('—', '–')
            parts = [part.strip() for part in clean_route.split('–')]
            
            if len(parts) >= 2:
                # Remove leading numbers from first part
                start_station = re.sub(r'^\d+\s+', '', parts[0]).strip()
                end_station = parts[-1].strip()
                
                print(f"   ✅ Parsed: {start_station} → {end_station}")
                
                # Create unique route key
                route_key = f"{start_station} → {end_station}"
                
                route_data = {
                    'route_header': route_header,
                    'start_station': start_station,
                    'end_station': end_station,
                    'page': row.get('page', 'N/A'),
                    'total_stations': row.get('total_stations', 'N/A'),
                    'route_key': route_key
                }
                
                all_route_data.append(route_data)
                
                # Track unique routes
                if route_key not in unique_routes:
                    unique_routes[route_key] = {
                        'start': start_station,
                        'end': end_station,
                        'count': 1,
                        'sample_route': route_header,
                        'pages': [row.get('page', 'N/A')],
                        'station_counts': [row.get('total_stations', 'N/A')]
                    }
                else:
                    unique_routes[route_key]['count'] += 1
                    unique_routes[route_key]['pages'].append(row.get('page', 'N/A'))
                    unique_routes[route_key]['station_counts'].append(row.get('total_stations', 'N/A'))
    
    return all_route_data, unique_routes

# Extract the pairs using the FIXED function
all_pairs, unique_pairs = extract_budapest_rajka_pairs_fixed()

print(f"\n🎯 FOUND {len(all_pairs)} BUDAPEST-RAJKA ROUTE ENTRIES")

if unique_pairs:
    print(f"\n🚂 UNIQUE BUDAPEST ↔ RAJKA PAIRS (Order Matters):")
    print("="*70)
    
    # Sort by start station name for better organization
    sorted_pairs = sorted(unique_pairs.items(), key=lambda x: x[1]['start'])
    
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        start = info['start']
        end = info['end'] 
        count = info['count']
        sample = info['sample_route']
        pages = info['pages'][:5]  # Show first 5 pages
        
        print(f"{i:2d}. {start} → {end}")
        print(f"    📊 Found {count} route instance(s)")
        print(f"    📄 Pages: {pages}")
        print(f"    🔗 Sample route: {sample}")
        print(f"    📏 Station counts: {info['station_counts'][:5]}")
        print()
    
    # Create DataFrame for the clean results
    unique_df = pd.DataFrame([
        {
            'direction': direction,
            'start_station': info['start'],
            'end_station': info['end'],
            'route_count': info['count'],
            'sample_route_header': info['sample_route'],
            'pages': ', '.join(map(str, info['pages'][:10])),  # First 10 pages as string
            'avg_stations': sum([x for x in info['station_counts'] if str(x).isdigit()]) / len([x for x in info['station_counts'] if str(x).isdigit()]) if [x for x in info['station_counts'] if str(x).isdigit()] else 0
        }
        for direction, info in unique_pairs.items()
    ])
    
    print(f"📊 SUMMARY STATISTICS:")
    print(f"   - Total unique directions: {len(unique_pairs)}")
    print(f"   - Total route instances: {sum(info['count'] for info in unique_pairs.values())}")
    if len(unique_df) > 0 and unique_df['avg_stations'].mean() > 0:
        print(f"   - Average stations per route: {unique_df['avg_stations'].mean():.1f}")
    
    # Save unique pairs to CSV
    timestamp = dt.datetime.now().strftime("%Y%m%d_%H%M%S")
    output_file = f"budapest_rajka_unique_pairs_{timestamp}.csv"
    unique_df.to_csv(output_file, index=False, encoding='utf-8')
    print(f"   💾 Saved to: {output_file}")
    
    # Show specifically Budapest → Rajka and Rajka → Budapest
    print(f"\n🎯 SPECIFIC BUDAPEST ↔ RAJKA DIRECTIONAL ANALYSIS:")
    
    budapest_to_rajka = []
    rajka_to_budapest = []
    
    for direction, info in unique_pairs.items():
        start_lower = info['start'].lower()
        end_lower = info['end'].lower()
        
        # Budapest → Rajka/Hegyeshalom
        if 'budapest' in start_lower and ('rajka' in end_lower or 'hegyeshalom' in end_lower):
            budapest_to_rajka.append(info)
        
        # Rajka/Hegyeshalom → Budapest  
        elif ('rajka' in start_lower or 'hegyeshalom' in start_lower) and 'budapest' in end_lower:
            rajka_to_budapest.append(info)
    
    print(f"   🔄 Budapest → Rajka/Hegyeshalom directions: {len(budapest_to_rajka)}")
    for pair in budapest_to_rajka:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    print(f"   🔄 Rajka/Hegyeshalom → Budapest directions: {len(rajka_to_budapest)}")  
    for pair in rajka_to_budapest:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    # Show the actual clean station pairs you wanted
    print(f"\n✅ FINAL ANSWER - UNIQUE BUDAPEST ↔ RAJKA PAIRS:")
    print("="*50)
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        print(f"{i}. {info['start']} → {info['end']}")
    
    print(f"\n🎉 SUCCESS! Found {len(unique_pairs)} unique directional pairs")
    print(f"📂 Detailed data saved to: {output_file}")
else:
    print("❌ No Budapest-Rajka pairs found. Check the data extraction.")


🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)
❌ No CSV files found. Please run the extraction first.


TypeError: object of type 'NoneType' has no len()

In [ ]:
# ========================= BUDAPEST ↔ RAJKA UNIQUE PAIRS =========================

def extract_budapest_rajka_pairs_fixed():
    """
    FIXED: Extract unique Budapest-Rajka pairs by parsing route headers correctly.
    The source/destination columns have parsing errors, so we use route_header instead.
    """
    print("🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)")
    print("="*60)
    
    # First, let's read the generated CSV file
    import glob
    
    # Find the most recent CSV file
    csv_files = glob.glob("mav_route_pairs_full_*.csv")
    if not csv_files:
        print("❌ No CSV files found. Please run the extraction first.")
        return None, None
    
    latest_csv = max(csv_files, key=lambda x: x.split('_')[-1])
    print(f"📂 Reading data from: {latest_csv}")
    
    # Read the CSV
    df_full = pd.read_csv(latest_csv, encoding='utf-8')
    print(f"📊 Total records in CSV: {len(df_full)}")
    
    # Show sample problematic data
    print(f"\n🔍 SAMPLE DATA (showing the parsing issues):")
    sample_data = df_full.head(3)
    for _, row in sample_data.iterrows():
        print(f"   Route: {row['route_header']}")
        print(f"   Source: {row['source']} (WRONG)")
        print(f"   Dest: {row['destination']} (WRONG)")
        print()
    
    print("💡 SOLUTION: Parse route headers directly instead of using source/destination")
    
    # Parse route headers directly
    unique_routes = {}
    all_route_data = []
    
    for _, row in df_full.iterrows():
        route_header = str(row.get('route_header', ''))
        
        # Only process Budapest-Rajka routes
        if not ('budapest' in route_header.lower() and 
               ('rajka' in route_header.lower() or 'hegyeshalom' in route_header.lower())):
            continue
        
        print(f"🔍 Processing: {route_header}")
        
        # Parse route header like "1 Budapest — Hegyeshalom — Rajka"
        if '—' in route_header or '–' in route_header:
            # Clean and split the route
            clean_route = route_header.replace('—', '–')
            parts = [part.strip() for part in clean_route.split('–')]
            
            if len(parts) >= 2:
                # Remove leading numbers from first part
                start_station = re.sub(r'^\d+\s+', '', parts[0]).strip()
                end_station = parts[-1].strip()
                
                print(f"   ✅ Parsed: {start_station} → {end_station}")
                
                # Create unique route key
                route_key = f"{start_station} → {end_station}"
                
                route_data = {
                    'route_header': route_header,
                    'start_station': start_station,
                    'end_station': end_station,
                    'page': row.get('page', 'N/A'),
                    'total_stations': row.get('total_stations', 'N/A'),
                    'route_key': route_key
                }
                
                all_route_data.append(route_data)
                
                # Track unique routes
                if route_key not in unique_routes:
                    unique_routes[route_key] = {
                        'start': start_station,
                        'end': end_station,
                        'count': 1,
                        'sample_route': route_header,
                        'pages': [row.get('page', 'N/A')],
                        'station_counts': [row.get('total_stations', 'N/A')]
                    }
                else:
                    unique_routes[route_key]['count'] += 1
                    unique_routes[route_key]['pages'].append(row.get('page', 'N/A'))
                    unique_routes[route_key]['station_counts'].append(row.get('total_stations', 'N/A'))
    
    return all_route_data, unique_routes

# Extract the pairs using the FIXED function
all_pairs, unique_pairs = extract_budapest_rajka_pairs_fixed()

print(f"\n🎯 FOUND {len(all_pairs)} BUDAPEST-RAJKA ROUTE ENTRIES")

if unique_pairs:
    print(f"\n🚂 UNIQUE BUDAPEST ↔ RAJKA PAIRS (Order Matters):")
    print("="*70)
    
    # Sort by start station name for better organization
    sorted_pairs = sorted(unique_pairs.items(), key=lambda x: x[1]['start'])
    
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        start = info['start']
        end = info['end'] 
        count = info['count']
        sample = info['sample_route']
        pages = info['pages'][:5]  # Show first 5 pages
        
        print(f"{i:2d}. {start} → {end}")
        print(f"    📊 Found {count} route instance(s)")
        print(f"    📄 Pages: {pages}")
        print(f"    🔗 Sample route: {sample}")
        print(f"    📏 Station counts: {info['station_counts'][:5]}")
        print()
    
    # Create DataFrame for the clean results
    unique_df = pd.DataFrame([
        {
            'direction': direction,
            'start_station': info['start'],
            'end_station': info['end'],
            'route_count': info['count'],
            'sample_route_header': info['sample_route'],
            'pages': ', '.join(map(str, info['pages'][:10])),  # First 10 pages as string
            'avg_stations': sum([x for x in info['station_counts'] if str(x).isdigit()]) / len([x for x in info['station_counts'] if str(x).isdigit()]) if [x for x in info['station_counts'] if str(x).isdigit()] else 0
        }
        for direction, info in unique_pairs.items()
    ])
    
    print(f"📊 SUMMARY STATISTICS:")
    print(f"   - Total unique directions: {len(unique_pairs)}")
    print(f"   - Total route instances: {sum(info['count'] for info in unique_pairs.values())}")
    if len(unique_df) > 0 and unique_df['avg_stations'].mean() > 0:
        print(f"   - Average stations per route: {unique_df['avg_stations'].mean():.1f}")
    
    # Save unique pairs to CSV
    timestamp = dt.datetime.now().strftime("%Y%m%d_%H%M%S")
    output_file = f"budapest_rajka_unique_pairs_{timestamp}.csv"
    unique_df.to_csv(output_file, index=False, encoding='utf-8')
    print(f"   💾 Saved to: {output_file}")
    
    # Show specifically Budapest → Rajka and Rajka → Budapest
    print(f"\n🎯 SPECIFIC BUDAPEST ↔ RAJKA DIRECTIONAL ANALYSIS:")
    
    budapest_to_rajka = []
    rajka_to_budapest = []
    
    for direction, info in unique_pairs.items():
        start_lower = info['start'].lower()
        end_lower = info['end'].lower()
        
        # Budapest → Rajka/Hegyeshalom
        if 'budapest' in start_lower and ('rajka' in end_lower or 'hegyeshalom' in end_lower):
            budapest_to_rajka.append(info)
        
        # Rajka/Hegyeshalom → Budapest  
        elif ('rajka' in start_lower or 'hegyeshalom' in start_lower) and 'budapest' in end_lower:
            rajka_to_budapest.append(info)
    
    print(f"   🔄 Budapest → Rajka/Hegyeshalom directions: {len(budapest_to_rajka)}")
    for pair in budapest_to_rajka:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    print(f"   🔄 Rajka/Hegyeshalom → Budapest directions: {len(rajka_to_budapest)}")  
    for pair in rajka_to_budapest:
        print(f"      • {pair['start']} → {pair['end']} ({pair['count']} route instances)")
    
    # Show the actual clean station pairs you wanted
    print(f"\n✅ FINAL ANSWER - UNIQUE BUDAPEST ↔ RAJKA PAIRS:")
    print("="*50)
    for i, (direction, info) in enumerate(sorted_pairs, 1):
        print(f"{i}. {info['start']} → {info['end']}")
    
    print(f"\n🎉 SUCCESS! Found {len(unique_pairs)} unique directional pairs")
    print(f"📂 Detailed data saved to: {output_file}")
else:
    print("❌ No Budapest-Rajka pairs found. Check the data extraction.")


🎯 EXTRACTING BUDAPEST ↔ RAJKA UNIQUE PAIRS (FIXED)
❌ No CSV files found. Please run the extraction first.


TypeError: object of type 'NoneType' has no len()

In [ ]:
# =============================================================================
# FIXED: Data Processing and Analysis
# This cell replaces any problematic code that tries to use local files
# =============================================================================

print("🔧 Processing loaded route data...")

# Convert loaded files to a more convenient format for analysis
route_data = []
station_pairs = set()

for file_info in files:
    station_pair = file_info['station_pair']
    data = file_info['data']
    timestamp = file_info['timestamp']
    
    station_pairs.add(station_pair)
    
    # Process each route in the file
    for route in data:
        route_info = {
            'station_pair': station_pair,
            'start_station': file_info['start_station'],
            'end_station': file_info['end_station'],
            'timestamp': timestamp,
            'filename': file_info['filename']
        }
        
        # Add route details if available
        if isinstance(route, dict):
            route_info.update(route)
        
        route_data.append(route_info)

print(f"📊 Processed {len(route_data)} routes from {len(station_pairs)} station pairs")
print(f"📅 Data timestamp range: {min([f['timestamp'] for f in files])} to {max([f['timestamp'] for f in files])}")

# Convert to DataFrame for easier analysis
df_routes = pd.DataFrame(route_data)
print(f"✅ Created DataFrame with {len(df_routes)} rows and {len(df_routes.columns)} columns")

# Display basic info about the dataset
print("\n📋 Dataset Overview:")
if len(df_routes) > 0:
    print(f"  • Total routes: {len(df_routes)}")
    print(f"  • Unique station pairs: {df_routes['station_pair'].nunique()}")
    print(f"  • Columns: {list(df_routes.columns)}")
    print(f"\n🔍 Sample data:")
    print(df_routes.head())
else:
    print("  ⚠️ No route data found in files")

# Basic statistics
if len(df_routes) > 0:
    print(f"\n📈 Basic Statistics:")
    print(f"  • Routes per station pair: {len(df_routes) / df_routes['station_pair'].nunique():.1f} average")
    print(f"  • Most common start station: {df_routes['start_station'].mode().iloc[0] if len(df_routes['start_station'].mode()) > 0 else 'N/A'}")
    print(f"  • Most common end station: {df_routes['end_station'].mode().iloc[0] if len(df_routes['end_station'].mode()) > 0 else 'N/A'}")

print("\n✅ Data processing complete - ready for analysis!")


In [ ]:
# =============================================================================
# ROUTE ANALYSIS AND VISUALIZATIONS
# =============================================================================

if len(df_routes) > 0:
    print("📈 Creating route analysis visualizations...")
    
    # Set up plotting style
    plt.style.use('default')
    sns.set_palette("husl")
    
    # Create subplots
    fig, axes = plt.subplots(2, 2, figsize=(15, 12))
    fig.suptitle('MAV Route Analysis Dashboard', fontsize=16, fontweight='bold')
    
    # 1. Station pair frequency
    station_pair_counts = df_routes['station_pair'].value_counts().head(10)
    axes[0, 0].bar(range(len(station_pair_counts)), station_pair_counts.values)
    axes[0, 0].set_title('Top 10 Station Pairs by Route Count')
    axes[0, 0].set_xlabel('Station Pair Rank')
    axes[0, 0].set_ylabel('Number of Routes')
    axes[0, 0].grid(True, alpha=0.3)
    
    # 2. Routes by start station
    start_station_counts = df_routes['start_station'].value_counts().head(10)
    axes[0, 1].barh(range(len(start_station_counts)), start_station_counts.values)
    axes[0, 1].set_title('Top 10 Start Stations')
    axes[0, 1].set_xlabel('Number of Routes')
    axes[0, 1].set_ylabel('Station Code')
    axes[0, 1].set_yticks(range(len(start_station_counts)))
    axes[0, 1].set_yticklabels(start_station_counts.index, fontsize=8)
    axes[0, 1].grid(True, alpha=0.3)
    
    # 3. Routes by end station
    end_station_counts = df_routes['end_station'].value_counts().head(10)
    axes[1, 0].barh(range(len(end_station_counts)), end_station_counts.values)
    axes[1, 0].set_title('Top 10 End Stations')
    axes[1, 0].set_xlabel('Number of Routes')
    axes[1, 0].set_ylabel('Station Code')
    axes[1, 0].set_yticks(range(len(end_station_counts)))
    axes[1, 0].set_yticklabels(end_station_counts.index, fontsize=8)
    axes[1, 0].grid(True, alpha=0.3)
    
    # 4. Data collection timeline (if we have timestamp data)
    if 'timestamp' in df_routes.columns:
        try:
            # Convert timestamp to datetime for plotting
            df_routes['datetime'] = pd.to_datetime(df_routes['timestamp'], format='%Y%m%d_%H%M%S')
            hourly_counts = df_routes['datetime'].dt.hour.value_counts().sort_index()
            
            axes[1, 1].plot(hourly_counts.index, hourly_counts.values, marker='o')
            axes[1, 1].set_title('Route Data Collection by Hour')
            axes[1, 1].set_xlabel('Hour of Day')
            axes[1, 1].set_ylabel('Number of Routes Collected')
            axes[1, 1].grid(True, alpha=0.3)
            axes[1, 1].set_xticks(range(0, 24, 2))
        except:
            # If timestamp parsing fails, show a simple count
            axes[1, 1].text(0.5, 0.5, 'Timestamp data\\nnot available\\nfor analysis', 
                           ha='center', va='center', transform=axes[1, 1].transAxes,
                           fontsize=12, bbox=dict(boxstyle="round,pad=0.3", facecolor="lightgray"))
            axes[1, 1].set_title('Data Collection Timeline')
    
    plt.tight_layout()
    plt.show()
    
    # Print summary statistics
    print(f"\n📊 SUMMARY STATISTICS:")
    print(f"=" * 50)
    print(f"📅 Data Date: {files[0]['timestamp'][:8] if files else 'Unknown'}")
    print(f"📁 Total Files Processed: {len(files)}")
    print(f"🚂 Total Routes Found: {len(df_routes)}")
    print(f"🚉 Unique Station Pairs: {df_routes['station_pair'].nunique()}")
    print(f"🎯 Unique Start Stations: {df_routes['start_station'].nunique()}")
    print(f"🏁 Unique End Stations: {df_routes['end_station'].nunique()}")
    
    print(f"\n🏆 TOP PERFORMERS:")
    print(f"Most Active Start Station: {start_station_counts.index[0]} ({start_station_counts.iloc[0]} routes)")
    print(f"Most Active End Station: {end_station_counts.index[0]} ({end_station_counts.iloc[0]} routes)")
    print(f"Busiest Route: {station_pair_counts.index[0]} ({station_pair_counts.iloc[0]} entries)")
    
    print(f"\n✅ Analysis complete! All data loaded successfully from Google Cloud Storage.")
    
else:
    print("❌ No route data available for analysis.")
    print("🔍 Please check that:")
    print("  • The Google Cloud Storage bucket contains data")
    print("  • The date parameter is correct")
    print("  • Your GCS authentication is working")
